In [ ]:
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [ ]:
import os

BASE_DIR = "/content/drive/MyDrive/AML Challenge"
os.chdir(BASE_DIR)
print("Current working directory:", os.getcwd())


Current working directory: /content/drive/MyDrive/AML Challenge


# PreProcessing

In [ ]:
import torch, torch.nn as nn, torch.nn.functional as F
from torch.utils.data import DataLoader, TensorDataset
from tqdm import tqdm
import numpy as np, pandas as pd
# ------------------------------------------------------
# 1. Device and data loading
# ------------------------------------------------------
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device:", device)

train_data = np.load(BASE_DIR+"/train.npz")
test_data  = np.load(BASE_DIR+"/test.clean.npz")

tx_train = train_data["captions/embeddings"]   # (125000, 1024)
im_train = train_data["images/embeddings"]     # (25000, 1536)
tx_test  = test_data["captions/embeddings"]    # (1500, 1024)

print("Train shapes:", tx_train.shape, im_train.shape)
print("Test shape:", tx_test.shape)

# ------------------------------------------------------
# 2. Match each caption to its corresponding image
# ------------------------------------------------------
repeat_factor = len(tx_train) // len(im_train)   # 5 captions per image
im_train_expanded = np.repeat(im_train, repeat_factor, axis=0)

Using device: cuda
Train shapes: (125000, 1024) (25000, 1536)
Test shape: (1500, 1024)


# Variational Autoencoder (VAE)
## Experiment 58: The "Giga-VAE."
# got score as Score: 0.86241

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader, TensorDataset
import numpy as np
import pandas as pd
from tqdm.auto import tqdm
import os
import time

# --- EXPERIMENT 58: "The Giga-VAE" ---
#
# This is a new probabilistic architecture inspired by the DALL-E 2 /
# CLIP Latents "prior" models.
# It learns a probabilistic mapping (A -> Distribution -> B) to
# handle the 1-to-5 text-to-image noise.
#
# 1. Architecture: NEW "VAETranslator"
# 2. Hidden Dim:   *** 8192 *** (Champion Horsepower)
# 3. Regularization: *** "GIGA-BOSS" ***
#    - Dropout:       0.4
#    - Weight Decay:  4e-4
#    - Mixup:         0.6
# 4. Time:         60 Epochs (Champion Sprint)
# 5. Loss:         CHAMPION Asymmetric Loss + *** KL Divergence Loss ***
# -----------------------------------------------------------------

# -----------------------------------------------------------------
# 1. Device and data loading (Same as before)
# -----------------------------------------------------------------
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

train_data = np.load("train.npz")
test_data  = np.load("test.clean.npz")

tx_train = train_data["captions/embeddings"]
im_train = train_data["images/embeddings"]
tx_test  = test_data["captions/embeddings"]

repeat_factor = len(tx_train) // len(im_train)
im_train_expanded = np.repeat(im_train, repeat_factor, axis=0)
print(f"Train shapes: {tx_train.shape}, {im_train.shape}, {im_train_expanded.shape}")
print(f"Test shape: {tx_test.shape}")

# -----------------------------------------------------------------
# 2. Data preprocessing (Same as before)
# -----------------------------------------------------------------
cpu_device = torch.device("cpu")
tx_train_t = torch.as_tensor(tx_train, dtype=torch.float32, device=cpu_device)
im_train_t_unique = torch.as_tensor(im_train, dtype=torch.float32, device=cpu_device)
tx_test_t  = torch.as_tensor(tx_test,  dtype=torch.float32, device=cpu_device)

tx_mean = tx_train_t.mean(0, keepdim=True)
im_mean = im_train_t_unique.mean(0, keepdim=True)

tx_train_t = F.normalize(tx_train_t - tx_mean, p=2, dim=1)
im_train_t_unique = F.normalize(im_train_t_unique - im_mean, p=2, dim=1)
tx_test_t = F.normalize(tx_test_t - tx_mean, p=2, dim=1)

im_train_exp = torch.as_tensor(im_train_expanded, dtype=torch.float32, device=cpu_device)
im_train_exp = F.normalize(im_train_exp - im_mean, p=2, dim=1)
print("Data preprocessed and normalized (on CPU).")

# -----------------------------------------------------------------
# 3. *** NEW: The VAE-Translator Model ***
# -----------------------------------------------------------------
class VAETranslator(nn.Module):
    def __init__(self, input_dim=1024, hidden_dim=8192, latent_dim=1536, output_dim=1536, dropout=0.4):
        super().__init__()
        self.latent_dim = latent_dim
        print(f"Initializing Giga-VAE (hidden_dim={hidden_dim}, latent_dim={latent_dim})")

        # --- ENCODER (Text -> Distribution) ---
        # 1024 -> 8192 -> 8192 -> (1536 * 2)
        self.encoder = nn.Sequential(
            nn.Linear(input_dim, hidden_dim),
            nn.GELU(),
            nn.LayerNorm(hidden_dim),
            nn.Dropout(dropout),

            nn.Linear(hidden_dim, hidden_dim),
            nn.GELU(),
            nn.LayerNorm(hidden_dim),
            nn.Dropout(dropout),

            nn.Linear(hidden_dim, latent_dim * 2) # Output mu and logvar
        )

        # --- DECODER (Distribution Sample -> Image) ---
        # 1536 -> 8192 -> 8192 -> 1536
        self.decoder = nn.Sequential(
            nn.Linear(latent_dim, hidden_dim),
            nn.GELU(),
            nn.LayerNorm(hidden_dim),
            nn.Dropout(dropout),

            nn.Linear(hidden_dim, hidden_dim),
            nn.GELU(),
            nn.LayerNorm(hidden_dim),
            nn.Dropout(dropout),

            nn.Linear(hidden_dim, output_dim)
        )

    def reparameterize(self, mu, logvar):
        std = torch.exp(0.5 * logvar)
        eps = torch.randn_like(std)
        return mu + eps * std

    def forward(self, x):
        # 1. Encode text to mu and logvar
        mu_logvar = self.encoder(x)
        mu = mu_logvar[..., :self.latent_dim]
        logvar = mu_logvar[..., self.latent_dim:]

        # 2. Get a sample 'z' from the distribution
        z = self.reparameterize(mu, logvar)

        # 3. Decode the sample to the image embedding space
        y_pred = self.decoder(z)

        # During training, return all parts for the loss function
        if self.training:
            return F.normalize(y_pred, p=2, dim=1), mu, logvar

        # During eval, just return the deterministic prediction
        # We use mu directly for a stable prediction
        y_pred_eval = self.decoder(mu)
        return F.normalize(y_pred_eval, p=2, dim=1)

# -----------------------------------------------------------------
# 4. Loss Functions (CHAMPION Loss + KL Divergence)
# -----------------------------------------------------------------
TAU = 0.01
MARGIN = 0.06
LOSS_WEIGHT_CONTRASTIVE = 0.7
LOSS_WEIGHT_TRIPLET = 0.3
MIXUP_ALPHA = 0.6 # Giga-Boss Mixup
KL_WEIGHT = 1e-5 # *** NEW: VAE Regularization Strength ***

triplet_loss_fn = nn.TripletMarginWithDistanceLoss(
    distance_function=lambda x, y: 1 - F.cosine_similarity(x, y),
    margin=MARGIN
)
print(f"Using CHAMPION ASYMMETRIC loss + *** VAE KL Loss (weight={KL_WEIGHT}) ***")

def calculate_kl_loss(mu, logvar):
    # KL divergence, VAE formula
    kl_loss = -0.5 * torch.sum(1 + logvar - mu.pow(2) - logvar.exp())
    # Return the *mean* loss per item in the batch
    return kl_loss / mu.size(0)

# -----------------------------------------------------------------
# 5. Validation split (Same as before)
# -----------------------------------------------------------------
N = len(tx_train_t)
val_size = int(0.1 * N)
idx_cpu = torch.randperm(N, device="cpu") # <-- New random seed for this run
val_idx, train_idx = idx_cpu[:val_size], idx_cpu[val_size:]

img_indices_train = (train_idx // 5)
img_indices_val = (val_idx // 5)

tx_val_t, im_val_t = tx_train_t[val_idx], im_train_exp[val_idx]
tx_train_t_sub, im_train_exp_sub = tx_train_t[train_idx], im_train_exp[train_idx]

train_dataset = TensorDataset(tx_train_t_sub, im_train_exp_sub, img_indices_train)
train_loader = DataLoader(train_dataset, batch_size=512, shuffle=True, num_workers=0)
print(f"Train pairs: {len(train_dataset)}, Validation pairs: {len(val_idx)}")

# -----------------------------------------------------------------
# 6. Memory-Safe Recall@K Utility (Same as before)
# -----------------------------------------------------------------
@torch.no_grad()
def recall_at_k(model, tx_queries, im_database, query_img_indices, chunk_size=1024, ks=(1, 5, 10, 50), k_csls=10):
    model.eval() # <-- This is CRITICAL. It tells the VAE to return deterministic preds
    device = next(model.parameters()).device
    all_correct_in_top_k = {k: [] for k in ks}

    Q_embed_list = []
    for i in range(0, len(tx_queries), chunk_size):
        chunk = tx_queries[i:i+chunk_size].to(device)
        Q_embed_list.append(model(chunk)) # model(chunk) will now return y_pred_eval
    Q_embed = torch.cat(Q_embed_list, dim=0)

    D_embed = im_database.to(device)

    mean_knn_d_list = []
    for i in tqdm(range(0, len(D_embed), 512), desc="CSLS (Pass 1/2)", leave=False):
        sim_T_chunk = D_embed[i:i+512] @ Q_embed.T
        knn_d_chunk = torch.topk(sim_T_chunk, k=k_csls, dim=1).values
        mean_knn_d_list.append(knn_d_chunk.mean(1))

    mean_knn_d = torch.cat(mean_knn_d_list, dim=0).unsqueeze(0)

    gt = query_img_indices.to(device)

    for i in tqdm(range(0, len(Q_embed), chunk_size), desc="CSLS (Pass 2/2)", leave=False):
        sim_chunk = Q_embed[i:i+chunk_size] @ D_embed.T
        gt_chunk = gt[i:i+chunk_size]

        knn_q_chunk = torch.topk(sim_chunk, k=k_csls, dim=1).values
        mean_knn_q = knn_q_chunk.mean(1, keepdim=True)

        csls_sim_chunk = 2 * sim_chunk - mean_knn_q - mean_knn_d

        top_indices_chunk = torch.argsort(csls_sim_chunk, dim=1, descending=True)

        for k in ks:
            top_k_preds = top_indices_chunk[:, :k]
            correct_in_top_k = (top_k_preds == gt_chunk.unsqueeze(1)).any(dim=1)
            all_correct_in_top_k[k].append(correct_in_top_k)

    recalls = {}
    for k in ks:
        recalls[f"R@{k}"] = torch.cat(all_correct_in_top_k[k]).float().mean().item()
    return recalls

# -----------------------------------------------------------------
# 7. *** NEW: Training Loop ***
# -----------------------------------------------------------------
EPOCHS = 60 # Champion "Sprint"
START_LR = 3e-4
WEIGHT_DECAY = 4e-4 # Giga-Boss Weight Decay
RUN_ID = f"giga_vae_model_{int(time.time())}"
FINAL_SAVE_PATH = f"giga_vae_model_{RUN_ID}_best.pth"

val_query_subset = tx_val_t[:5000]
val_indices_subset = img_indices_val[:5000]
val_db_subset = im_train_t_unique

# --- Initialize the new Giga-VAE model ---
model = VAETranslator(dropout=0.4, hidden_dim=8192, latent_dim=1536, output_dim=1536).to(device)

optimizer = torch.optim.AdamW(model.parameters(), lr=START_LR, weight_decay=WEIGHT_DECAY)
scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=EPOCHS)
scaler = torch.amp.GradScaler('cuda')

print(f"\n--- Starting New Architecture: Giga-VAE (RUN {RUN_ID}) ---")
print(f"Training (Epochs: {EPOCHS}, LR={START_LR}, WD={WEIGHT_DECAY}, Mixup={MIXUP_ALPHA})...\n")

best_val_r10 = 0.0
for epoch in range(1, EPOCHS + 1):
    model.train() # <-- This is CRITICAL. It tells the VAE to return all 3 outputs
    total_recon_loss = 0.0
    total_kl_loss = 0.0

    for x_batch, y_batch, img_indices in tqdm(train_loader, desc=f"Epoch {epoch:03d}/{EPOCHS}", leave=False):
        x_batch = x_batch.to(device)
        y_batch = y_batch.to(device)

        # --- GIGA-BOSS MIXUP IMPLEMENTATION ---
        idx_shuffle = torch.randperm(x_batch.size(0))
        lam = np.random.beta(MIXUP_ALPHA, MIXUP_ALPHA)
        x_mix = lam * x_batch + (1 - lam) * x_batch[idx_shuffle]
        y_mix = F.normalize(lam * y_batch + (1 - lam) * y_batch[idx_shuffle], p=2, dim=1)

        optimizer.zero_grad()
        with torch.amp.autocast('cuda'):
            # --- VAE FORWARD PASS ---
            y_pred, mu, logvar = model(x_mix) # Model is in .train() mode

            # --- 1. Reconstruction Loss (Our Champion Loss) ---
            sims_with_tau = y_pred @ y_mix.T / TAU
            labels = torch.arange(y_pred.size(0), device=device)
            loss_con = F.cross_entropy(sims_with_tau, labels)

            with torch.no_grad():
                sims_no_tau = y_pred @ y_mix.T
                positive_mask = torch.eye(y_batch.size(0), dtype=torch.bool, device=device)
                sims_no_tau.masked_fill_(positive_mask, -float('inf'))
                hard_neg_idx = sims_no_tau.argmax(dim=1)
            y_hard_neg = y_mix[hard_neg_idx]
            loss_tri = triplet_loss_fn(y_pred, y_mix, y_hard_neg)

            recon_loss = (LOSS_WEIGHT_CONTRASTIVE * loss_con) + (LOSS_WEIGHT_TRIPLET * loss_tri)

            # --- 2. KL Divergence Loss ---
            kl_loss = calculate_kl_loss(mu, logvar)

            # --- 3. Total Loss ---
            loss = recon_loss + (KL_WEIGHT * kl_loss)

        scaler.scale(loss).backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)
        scaler.step(optimizer)
        scaler.update()

        total_recon_loss += recon_loss.item()
        total_kl_loss += kl_loss.item()

    current_lr = scheduler.get_last_lr()[0]
    scheduler.step()
    avg_recon_loss = total_recon_loss / len(train_loader)
    avg_kl_loss = total_kl_loss / len(train_loader)

    # ----- Validation (quick subset) -----
    rec = recall_at_k(model, val_query_subset, val_db_subset, val_indices_subset, chunk_size=1024)
    current_r10 = rec['R@10']

    save_marker = ""
    if current_r10 > best_val_r10:
        best_val_r10 = current_r10
        torch.save(model.state_dict(), FINAL_SAVE_PATH)
        save_marker = "<- Best R@10! Saved."

    print(f"Epoch {epoch:03d}: ReconLoss={avg_recon_loss:.4f} KL_Loss={avg_kl_loss:.2f} (LR={current_lr:.1E}) | R@10(Val)={current_r10:.4f} {save_marker}")

print(f"\n🎯 Training complete. Best model (R@10={best_val_r10:.4f}) saved as {FINAL_SAVE_PATH}")

# -----------------------------------------------------------------
# 8. Inference + Submission
# -----------------------------------------------------------------
print(f"Loading BEST model from {FINAL_SAVE_PATH} for inference...")
model = VAETranslator(dropout=0.4, hidden_dim=8192, latent_dim=1536, output_dim=1536).to(device)
model.load_state_dict(torch.load(FINAL_SAVE_PATH))
model.eval() # <-- This is CRITICAL. Ensures model(chunk) gives deterministic output
print("Best model loaded.")

with torch.no_grad():
    preds_list = []
    for i in tqdm(range(0, len(tx_test_t), 1024), desc="Generating Sub"):
        chunk = tx_test_t[i:i+1024].to(device)
        preds_list.append(model(chunk)) # model is in .eval() mode
    preds = torch.cat(preds_list, dim=0).cpu().numpy()

test_ids = test_data["captions/ids"].astype(int)
submission = pd.DataFrame({
    "id": test_ids,
    "embedding": [list(map(float, row)) for row in preds]
})

submission_filename = f"submission_giga_vae_run_{RUN_ID}.csv"
submission.to_csv(submission_filename, index=False)
print(f"\n✅ {submission_filename} saved successfully.")

# --- Final Validation (on FULL val set, now OOM-safe) ---
print("Calculating final validation scores on full val set...")
rec_full = recall_at_k(model, tx_val_t, im_train_t_unique, img_indices_val, chunk_size=1024)
print("\n--- Full Validation Results ---")
print(f"Validation Recall@1:  {rec_full['R@1']:<8.4f}")
print(f"Validation Recall@5:  {rec_full['R@5']:<8.4f}")
print(f"Validation Recall@10: {rec_full['R@10']:<8.4f}")
print(f"Validation Recall@50: {rec_full['R@50']:<8.4f}")

Using device: cuda
Train shapes: (125000, 1024), (25000, 1536), (125000, 1536)
Test shape: (1500, 1024)
Data preprocessed and normalized (on CPU).
Using CHAMPION ASYMMETRIC loss + *** VAE KL Loss (weight=1e-05) ***
Train pairs: 112500, Validation pairs: 12500
Initializing Giga-VAE (hidden_dim=8192, latent_dim=1536)

--- Starting New Architecture: Giga-VAE (RUN giga_vae_model_1762268434) ---
Training (Epochs: 60, LR=0.0003, WD=0.0004, Mixup=0.6)...



Epoch 001/60:   0%|          | 0/220 [00:00<?, ?it/s]

CSLS (Pass 1/2):   0%|          | 0/49 [00:00<?, ?it/s]

CSLS (Pass 2/2):   0%|          | 0/5 [00:00<?, ?it/s]

Epoch 001: ReconLoss=2.6223 KL_Loss=1208.27 (LR=3.0E-04) | R@10(Val)=0.3122 <- Best R@10! Saved.


...

Generating Sub:   0%|          | 0/2 [00:00<?, ?it/s]


✅ submission_giga_vae_run_giga_vae_model_1762268434.csv saved successfully.
Calculating final validation scores on full val set...


CSLS (Pass 1/2):   0%|          | 0/49 [00:00<?, ?it/s]

CSLS (Pass 2/2):   0%|          | 0/13 [00:00<?, ?it/s]


--- Full Validation Results ---
Validation Recall@1:  0.3070  
Validation Recall@5:  0.5630  
Validation Recall@10: 0.6671  
Validation Recall@50: 0.8613  


#

# Fine tune on previous VAE

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader, TensorDataset
import numpy as np
import pandas as pd
from tqdm.auto import tqdm
import os
import time

# --- EXPERIMENT 59: "The Giga-VAE" (Looser Brakes) ---
#
# 1. Architecture: CHAMPION "Giga-VAE"
# 2. All "Giga-Boss" settings: hidden_dim=8192, DO=0.4, WD=4e-4, Mixup=0.6
# 3. Time:         60 Epochs
# 4. Loss Change:  *** KL_WEIGHT = 1e-6 *** (Was 1e-5)
# 5. RUN_ID:       *** VAE_exp2 ***
# -----------------------------------------------------------------

# -----------------------------------------------------------------
# 1. Device and data loading
# -----------------------------------------------------------------
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

if not os.path.exists("train.npz") or not os.path.exists("test.clean.npz"):
    print("ERROR: 'train.npz' or 'test.clean.npz' not found.")
    print("Please make sure these files are in the same directory as your script.")
    # You might want to raise an error here to stop the script
    # raise FileNotFoundError("Required data files not found.")
else:
    print("Found 'train.npz' and 'test.clean.npz'. Loading data...")

train_data = np.load("train.npz")
test_data  = np.load("test.clean.npz")

tx_train = train_data["captions/embeddings"]
im_train = train_data["images/embeddings"]
tx_test  = test_data["captions/embeddings"]

repeat_factor = len(tx_train) // len(im_train)
im_train_expanded = np.repeat(im_train, repeat_factor, axis=0)
print(f"Train shapes: {tx_train.shape}, {im_train.shape}, {im_train_expanded.shape}")
print(f"Test shape: {tx_test.shape}")

# -----------------------------------------------------------------
# 2. Data preprocessing
# -----------------------------------------------------------------
cpu_device = torch.device("cpu")
tx_train_t = torch.as_tensor(tx_train, dtype=torch.float32, device=cpu_device)
im_train_t_unique = torch.as_tensor(im_train, dtype=torch.float32, device=cpu_device)
tx_test_t  = torch.as_tensor(tx_test,  dtype=torch.float32, device=cpu_device)

tx_mean = tx_train_t.mean(0, keepdim=True)
im_mean = im_train_t_unique.mean(0, keepdim=True)

tx_train_t = F.normalize(tx_train_t - tx_mean, p=2, dim=1)
im_train_t_unique = F.normalize(im_train_t_unique - im_mean, p=2, dim=1)
tx_test_t = F.normalize(tx_test_t - tx_mean, p=2, dim=1)

im_train_exp = torch.as_tensor(im_train_expanded, dtype=torch.float32, device=cpu_device)
im_train_exp = F.normalize(im_train_exp - im_mean, p=2, dim=1)
print("Data preprocessed and normalized (on CPU).")

# -----------------------------------------------------------------
# 3. The Giga-VAE Model
# -----------------------------------------------------------------
class VAETranslator(nn.Module):
    def __init__(self, input_dim=1024, hidden_dim=8192, latent_dim=1536, output_dim=1536, dropout=0.4):
        super().__init__()
        self.latent_dim = latent_dim
        print(f"Initializing Giga-VAE (hidden_dim={hidden_dim}, latent_dim={latent_dim})")

        # --- ENCODER (Text -> Distribution) ---
        self.encoder = nn.Sequential(
            nn.Linear(input_dim, hidden_dim),
            nn.GELU(),
            nn.LayerNorm(hidden_dim),
            nn.Dropout(dropout),
            nn.Linear(hidden_dim, hidden_dim),
            nn.GELU(),
            nn.LayerNorm(hidden_dim),
            nn.Dropout(dropout),
            nn.Linear(hidden_dim, latent_dim * 2) # Output mu and logvar
        )

        # --- DECODER (Distribution Sample -> Image) ---
        self.decoder = nn.Sequential(
            nn.Linear(latent_dim, hidden_dim),
            nn.GELU(),
            nn.LayerNorm(hidden_dim),
            nn.Dropout(dropout),
            nn.Linear(hidden_dim, hidden_dim),
            nn.GELU(),
            nn.LayerNorm(hidden_dim),
            nn.Dropout(dropout),
            nn.Linear(hidden_dim, output_dim)
        )

    def reparameterize(self, mu, logvar):
        std = torch.exp(0.5 * logvar)
        eps = torch.randn_like(std)
        return mu + eps * std

    def forward(self, x):
        mu_logvar = self.encoder(x)
        mu = mu_logvar[..., :self.latent_dim]
        logvar = mu_logvar[..., self.latent_dim:]

        if self.training:
            z = self.reparameterize(mu, logvar)
            y_pred = self.decoder(z)
            return F.normalize(y_pred, p=2, dim=1), mu, logvar

        # During eval, use mu directly for a stable prediction
        y_pred_eval = self.decoder(mu)
        return F.normalize(y_pred_eval, p=2, dim=1)

# -----------------------------------------------------------------
# 4. Loss Functions
# -----------------------------------------------------------------
TAU = 0.01
MARGIN = 0.06
LOSS_WEIGHT_CONTRASTIVE = 0.7
LOSS_WEIGHT_TRIPLET = 0.3
MIXUP_ALPHA = 0.6 # Giga-Boss Mixup
KL_WEIGHT = 1e-6 # *** NEW: 10x WEAKER BRAKE ***

triplet_loss_fn = nn.TripletMarginWithDistanceLoss(
    distance_function=lambda x, y: 1 - F.cosine_similarity(x, y),
    margin=MARGIN
)
print(f"Using CHAMPION ASYMMETRIC loss + VAE KL Loss (weight={KL_WEIGHT})")

def calculate_kl_loss(mu, logvar):
    kl_loss = -0.5 * torch.sum(1 + logvar - mu.pow(2) - logvar.exp())
    return kl_loss / mu.size(0)

# -----------------------------------------------------------------
# 5. Validation split
# -----------------------------------------------------------------
N = len(tx_train_t)
val_size = int(0.1 * N)
idx_cpu = torch.randperm(N, device="cpu") # <-- New random seed for this run
val_idx, train_idx = idx_cpu[:val_size], idx_cpu[val_size:]

img_indices_train = (train_idx // 5)
img_indices_val = (val_idx // 5)

tx_val_t, im_val_t = tx_train_t[val_idx], im_train_exp[val_idx]
tx_train_t_sub, im_train_exp_sub = tx_train_t[train_idx], im_train_exp[train_idx]

train_dataset = TensorDataset(tx_train_t_sub, im_train_exp_sub, img_indices_train)
train_loader = DataLoader(train_dataset, batch_size=512, shuffle=True, num_workers=0)
print(f"Train pairs: {len(train_dataset)}, Validation pairs: {len(val_idx)}")

# -----------------------------------------------------------------
# 6. Memory-Safe Recall@K Utility
# -----------------------------------------------------------------
@torch.no_grad()
def recall_at_k(model, tx_queries, im_database, query_img_indices, chunk_size=1024, ks=(1, 5, 10, 50), k_csls=10):
    model.eval()
    device = next(model.parameters()).device
    all_correct_in_top_k = {k: [] for k in ks}

    Q_embed_list = []
    for i in range(0, len(tx_queries), chunk_size):
        chunk = tx_queries[i:i+chunk_size].to(device)
        Q_embed_list.append(model(chunk))
    Q_embed = torch.cat(Q_embed_list, dim=0)

    D_embed = im_database.to(device)

    mean_knn_d_list = []
    for i in tqdm(range(0, len(D_embed), 512), desc="CSLS (Pass 1/2)", leave=False):
        sim_T_chunk = D_embed[i:i+512] @ Q_embed.T
        knn_d_chunk = torch.topk(sim_T_chunk, k=k_csls, dim=1).values
        mean_knn_d_list.append(knn_d_chunk.mean(1))

    mean_knn_d = torch.cat(mean_knn_d_list, dim=0).unsqueeze(0)

    gt = query_img_indices.to(device)

    for i in tqdm(range(0, len(Q_embed), chunk_size), desc="CSLS (Pass 2/2)", leave=False):
        sim_chunk = Q_embed[i:i+chunk_size] @ D_embed.T
        gt_chunk = gt[i:i+chunk_size]

        knn_q_chunk = torch.topk(sim_chunk, k=k_csls, dim=1).values
        mean_knn_q = knn_q_chunk.mean(1, keepdim=True)

        csls_sim_chunk = 2 * sim_chunk - mean_knn_q - mean_knn_d

        top_indices_chunk = torch.argsort(csls_sim_chunk, dim=1, descending=True)

        for k in ks:
            top_k_preds = top_indices_chunk[:, :k]
            correct_in_top_k = (top_k_preds == gt_chunk.unsqueeze(1)).any(dim=1)
            all_correct_in_top_k[k].append(correct_in_top_k)

    recalls = {}
    for k in ks:
        recalls[f"R@{k}"] = torch.cat(all_correct_in_top_k[k]).float().mean().item()
    return recalls

# -----------------------------------------------------------------
# 7. Training Loop
# -----------------------------------------------------------------
EPOCHS = 60
START_LR = 3e-4
WEIGHT_DECAY = 4e-4

# --- MODIFICATION: Your specific RUN_ID ---
RUN_ID = "VAE_exp2"
FINAL_SAVE_PATH = f"{RUN_ID}_best.pth"
# --- END MODIFICATION ---

val_query_subset = tx_val_t[:5000]
val_indices_subset = img_indices_val[:5000]
val_db_subset = im_train_t_unique

model = VAETranslator(dropout=0.4, hidden_dim=8192, latent_dim=1536, output_dim=1536).to(device)

optimizer = torch.optim.AdamW(model.parameters(), lr=START_LR, weight_decay=WEIGHT_DECAY)
scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=EPOCHS)
scaler = torch.amp.GradScaler('cuda')

print(f"\n--- Starting Giga-VAE (Looser Brakes, KL_WEIGHT=1e-6) (RUN {RUN_ID}) ---")
print(f"Training (Epochs: {EPOCHS}, LR={START_LR}, WD={WEIGHT_DECAY}, Mixup={MIXUP_ALPHA})...\n")

best_val_r10 = 0.0
for epoch in range(1, EPOCHS + 1):
    model.train()
    total_recon_loss = 0.0
    total_kl_loss = 0.0

    for x_batch, y_batch, img_indices in tqdm(train_loader, desc=f"Epoch {epoch:03d}/{EPOCHS}", leave=False):
        x_batch = x_batch.to(device)
        y_batch = y_batch.to(device)

        idx_shuffle = torch.randperm(x_batch.size(0))
        lam = np.random.beta(MIXUP_ALPHA, MIXUP_ALPHA)
        x_mix = lam * x_batch + (1 - lam) * x_batch[idx_shuffle]
        y_mix = F.normalize(lam * y_batch + (1 - lam) * y_batch[idx_shuffle], p=2, dim=1)

        optimizer.zero_grad()
        with torch.amp.autocast('cuda'):
            y_pred, mu, logvar = model(x_mix)

            # --- 1. Reconstruction Loss ---
            sims_with_tau = y_pred @ y_mix.T / TAU
            labels = torch.arange(y_pred.size(0), device=device)
            loss_con = F.cross_entropy(sims_with_tau, labels)

            with torch.no_grad():
                sims_no_tau = y_pred @ y_mix.T
                positive_mask = torch.eye(y_batch.size(0), dtype=torch.bool, device=device)
                sims_no_tau.masked_fill_(positive_mask, -float('inf'))
                hard_neg_idx = sims_no_tau.argmax(dim=1)
            y_hard_neg = y_mix[hard_neg_idx]
            loss_tri = triplet_loss_fn(y_pred, y_mix, y_hard_neg)

            recon_loss = (LOSS_WEIGHT_CONTRASTIVE * loss_con) + (LOSS_WEIGHT_TRIPLET * loss_tri)

            # --- 2. KL Divergence Loss ---
            kl_loss = calculate_kl_loss(mu, logvar)

            # --- 3. Total Loss ---
            loss = recon_loss + (KL_WEIGHT * kl_loss) # KL_WEIGHT is now 1e-6

        scaler.scale(loss).backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)
        scaler.step(optimizer)
        scaler.update()

        total_recon_loss += recon_loss.item()
        total_kl_loss += kl_loss.item()

    current_lr = scheduler.get_last_lr()[0]
    scheduler.step()
    avg_recon_loss = total_recon_loss / len(train_loader)
    avg_kl_loss = total_kl_loss / len(train_loader)

    # ----- Validation (quick subset) -----
    rec = recall_at_k(model, val_query_subset, val_db_subset, val_indices_subset, chunk_size=1024)
    current_r10 = rec['R@10']

    save_marker = ""
    if current_r10 > best_val_r10:
        best_val_r10 = current_r10
        torch.save(model.state_dict(), FINAL_SAVE_PATH)
        save_marker = "<- Best R@10! Saved."

    print(f"Epoch {epoch:03d}: ReconLoss={avg_recon_loss:.4f} KL_Loss={avg_kl_loss:.2f} (LR={current_lr:.1E}) | R@10(Val)={current_r10:.4f} {save_marker}")

print(f"\n🎯 Training complete. Best model (R@10={best_val_r10:.4f}) saved as {FINAL_SAVE_PATH}")

# -----------------------------------------------------------------
# 8. Inference + Submission
# -----------------------------------------------------------------
print(f"Loading BEST model from {FINAL_SAVE_PATH} for inference...")
model = VAETranslator(dropout=0.4, hidden_dim=8192, latent_dim=1536, output_dim=1536).to(device)
model.load_state_dict(torch.load(FINAL_SAVE_PATH))
model.eval()
print("Best model loaded.")

with torch.no_grad():
    preds_list = []
    for i in tqdm(range(0, len(tx_test_t), 1024), desc="Generating Sub"):
        chunk = tx_test_t[i:i+1024].to(device)
        preds_list.append(model(chunk))

    preds = torch.cat(preds_list, dim=0).cpu().numpy()

test_ids = test_data["captions/ids"].astype(int)
submission = pd.DataFrame({
    "id": test_ids,
    "embedding": [list(map(float, row)) for row in preds]
})

# --- MODIFICATION: Your specific submission filename ---
submission_filename = f"submission_{RUN_ID}.csv"
submission.to_csv(submission_filename, index=False)
print(f"\n✅ {submission_filename} saved successfully.")

# --- Final Validation (on FULL val set, now OOM-safe) ---
print("Calculating final validation scores on full val set...")
rec_full = recall_at_k(model, tx_val_t, im_train_t_unique, img_indices_val, chunk_size=1024)
print("\n--- Full Validation Results ---")
print(f"Validation Recall@1:  {rec_full['R@1']:<8.4f}")
print(f"Validation Recall@5:  {rec_full['R@5']:<8.4f}")
print(f"Validation Recall@10: {rec_full['R@10']:<8.4f}")
print(f"Validation Recall@50: {rec_full['R@50']:<8.4f}")

Using device: cuda
Found 'train.npz' and 'test.clean.npz'. Loading data...
Train shapes: (125000, 1024), (25000, 1536), (125000, 1536)
Test shape: (1500, 1024)
Data preprocessed and normalized (on CPU).
Using CHAMPION ASYMMETRIC loss + VAE KL Loss (weight=1e-06)
Train pairs: 112500, Validation pairs: 12500
Initializing Giga-VAE (hidden_dim=8192, latent_dim=1536)

--- Starting Giga-VAE (Looser Brakes, KL_WEIGHT=1e-6) (RUN VAE_exp2) ---
Training (Epochs: 60, LR=0.0003, WD=0.0004, Mixup=0.6)...



Epoch 001/60:   0%|          | 0/220 [00:00<?, ?it/s]

CSLS (Pass 1/2):   0%|          | 0/49 [00:00<?, ?it/s]

CSLS (Pass 2/2):   0%|          | 0/5 [00:00<?, ?it/s]

Epoch 001: ReconLoss=2.6321 KL_Loss=1213.50 (LR=3.0E-04) | R@10(Val)=0.3082 <- Best R@10! Saved.


...

Generating Sub:   0%|          | 0/2 [00:00<?, ?it/s]


✅ submission_VAE_exp2.csv saved successfully.
Calculating final validation scores on full val set...


CSLS (Pass 1/2):   0%|          | 0/49 [00:00<?, ?it/s]

CSLS (Pass 2/2):   0%|          | 0/13 [00:00<?, ?it/s]


--- Full Validation Results ---
Validation Recall@1:  0.3002  
Validation Recall@5:  0.5590  
Validation Recall@10: 0.6649  
Validation Recall@50: 0.8632  


# EXP3 - VAE with hidden_dim = 2048 and high Braker KL_WEIGHT=5e-5

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader, TensorDataset
import numpy as np
import pandas as pd
from tqdm.auto import tqdm
import os
import time

# --- EXPERIMENT 60: "The Giga-VAE" (Tighter Brakes) ---
#
# VAE_exp1 (KL=1e-5) scored 0.86241
# VAE_exp2 (KL=1e-6) scored 0.85748
# This means MORE regularization (a stronger brake) is BETTER.
#
# 1. Architecture: CHAMPION "Giga-VAE"
# 2. All "Giga-Boss" settings: hidden_dim=8192, DO=0.4, WD=4e-4, Mixup=0.6
# 3. Time:         60 Epochs
# 4. Loss Change:  *** KL_WEIGHT = 5e-5 *** (Was 1e-5. We are tightening the brake)
# 5. RUN_ID:       *** VAE_exp3 ***
# -----------------------------------------------------------------

# -----------------------------------------------------------------
# 1. Device and data loading
# -----------------------------------------------------------------
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

if not os.path.exists("train.npz") or not os.path.exists("test.clean.npz"):
    print("ERROR: 'train.npz' or 'test.clean.npz' not found.")
    raise FileNotFoundError("Required data files not found.")
else:
    print("Found 'train.npz' and 'test.clean.npz'. Loading data...")

train_data = np.load("train.npz")
test_data  = np.load("test.clean.npz")

tx_train = train_data["captions/embeddings"]
im_train = train_data["images/embeddings"]
tx_test  = test_data["captions/embeddings"]

repeat_factor = len(tx_train) // len(im_train)
im_train_expanded = np.repeat(im_train, repeat_factor, axis=0)
print(f"Train shapes: {tx_train.shape}, {im_train.shape}, {im_train_expanded.shape}")
print(f"Test shape: {tx_test.shape}")

# -----------------------------------------------------------------
# 2. Data preprocessing
# -----------------------------------------------------------------
cpu_device = torch.device("cpu")
tx_train_t = torch.as_tensor(tx_train, dtype=torch.float32, device=cpu_device)
im_train_t_unique = torch.as_tensor(im_train, dtype=torch.float32, device=cpu_device)
tx_test_t  = torch.as_tensor(tx_test,  dtype=torch.float32, device=cpu_device)

tx_mean = tx_train_t.mean(0, keepdim=True)
im_mean = im_train_t_unique.mean(0, keepdim=True)

tx_train_t = F.normalize(tx_train_t - tx_mean, p=2, dim=1)
im_train_t_unique = F.normalize(im_train_t_unique - im_mean, p=2, dim=1)
tx_test_t = F.normalize(tx_test_t - tx_mean, p=2, dim=1)

im_train_exp = torch.as_tensor(im_train_expanded, dtype=torch.float32, device=cpu_device)
im_train_exp = F.normalize(im_train_exp - im_mean, p=2, dim=1)
print("Data preprocessed and normalized (on CPU).")

# -----------------------------------------------------------------
# 3. The Giga-VAE Model
# -----------------------------------------------------------------
class VAETranslator(nn.Module):
    def __init__(self, input_dim=1024, hidden_dim=8192, latent_dim=1536, output_dim=1536, dropout=0.4):
        super().__init__()
        self.latent_dim = latent_dim
        print(f"Initializing Giga-VAE (hidden_dim={hidden_dim}, latent_dim={latent_dim})")

        # --- ENCODER (Text -> Distribution) ---
        self.encoder = nn.Sequential(
            nn.Linear(input_dim, hidden_dim),
            nn.GELU(),
            nn.LayerNorm(hidden_dim),
            nn.Dropout(dropout),
            nn.Linear(hidden_dim, hidden_dim),
            nn.GELU(),
            nn.LayerNorm(hidden_dim),
            nn.Dropout(dropout),
            nn.Linear(hidden_dim, latent_dim * 2) # Output mu and logvar
        )

        # --- DECODER (Distribution Sample -> Image) ---
        self.decoder = nn.Sequential(
            nn.Linear(latent_dim, hidden_dim),
            nn.GELU(),
            nn.LayerNorm(hidden_dim),
            nn.Dropout(dropout),
            nn.Linear(hidden_dim, hidden_dim),
            nn.GELU(),
            nn.LayerNorm(hidden_dim),
            nn.Dropout(dropout),
            nn.Linear(hidden_dim, output_dim)
        )

    def reparameterize(self, mu, logvar):
        std = torch.exp(0.5 * logvar)
        eps = torch.randn_like(std)
        return mu + eps * std

    def forward(self, x):
        mu_logvar = self.encoder(x)
        mu = mu_logvar[..., :self.latent_dim]
        logvar = mu_logvar[..., self.latent_dim:]

        if self.training:
            z = self.reparameterize(mu, logvar)
            y_pred = self.decoder(z)
            return F.normalize(y_pred, p=2, dim=1), mu, logvar

        # During eval, use mu directly for a stable prediction
        y_pred_eval = self.decoder(mu)
        return F.normalize(y_pred_eval, p=2, dim=1)

# -----------------------------------------------------------------
# 4. Loss Functions
# -----------------------------------------------------------------
TAU = 0.01
MARGIN = 0.06
LOSS_WEIGHT_CONTRASTIVE = 0.7
LOSS_WEIGHT_TRIPLET = 0.3
MIXUP_ALPHA = 0.6 # Giga-Boss Mixup
KL_WEIGHT = 5e-5 # *** NEW: 5x STRONGER BRAKE ***

triplet_loss_fn = nn.TripletMarginWithDistanceLoss(
    distance_function=lambda x, y: 1 - F.cosine_similarity(x, y),
    margin=MARGIN
)
print(f"Using CHAMPION ASYMMETRIC loss + VAE KL Loss (weight={KL_WEIGHT})")

def calculate_kl_loss(mu, logvar):
    kl_loss = -0.5 * torch.sum(1 + logvar - mu.pow(2) - logvar.exp())
    return kl_loss / mu.size(0)

# -----------------------------------------------------------------
# 5. Validation split
# -----------------------------------------------------------------
N = len(tx_train_t)
val_size = int(0.1 * N)
idx_cpu = torch.randperm(N, device="cpu") # <-- New random seed for this run
val_idx, train_idx = idx_cpu[:val_size], idx_cpu[val_size:]

img_indices_train = (train_idx // 5)
img_indices_val = (val_idx // 5)

tx_val_t, im_val_t = tx_train_t[val_idx], im_train_exp[val_idx]
tx_train_t_sub, im_train_exp_sub = tx_train_t[train_idx], im_train_exp[train_idx]

train_dataset = TensorDataset(tx_train_t_sub, im_train_exp_sub, img_indices_train)
train_loader = DataLoader(train_dataset, batch_size=512, shuffle=True, num_workers=0)
print(f"Train pairs: {len(train_dataset)}, Validation pairs: {len(val_idx)}")

# -----------------------------------------------------------------
# 6. Memory-Safe Recall@K Utility
# -----------------------------------------------------------------
@torch.no_grad()
def recall_at_k(model, tx_queries, im_database, query_img_indices, chunk_size=1024, ks=(1, 5, 10, 50), k_csls=10):
    model.eval()
    device = next(model.parameters()).device
    all_correct_in_top_k = {k: [] for k in ks}

    Q_embed_list = []
    for i in range(0, len(tx_queries), chunk_size):
        chunk = tx_queries[i:i+chunk_size].to(device)
        Q_embed_list.append(model(chunk))
    Q_embed = torch.cat(Q_embed_list, dim=0)

    D_embed = im_database.to(device)

    mean_knn_d_list = []
    for i in tqdm(range(0, len(D_embed), 512), desc="CSLS (Pass 1/2)", leave=False):
        sim_T_chunk = D_embed[i:i+512] @ Q_embed.T
        knn_d_chunk = torch.topk(sim_T_chunk, k=k_csls, dim=1).values
        mean_knn_d_list.append(knn_d_chunk.mean(1))

    mean_knn_d = torch.cat(mean_knn_d_list, dim=0).unsqueeze(0)

    gt = query_img_indices.to(device)

    for i in tqdm(range(0, len(Q_embed), chunk_size), desc="CSLS (Pass 2/2)", leave=False):
        sim_chunk = Q_embed[i:i+chunk_size] @ D_embed.T
        gt_chunk = gt[i:i+chunk_size]

        knn_q_chunk = torch.topk(sim_chunk, k=k_csls, dim=1).values
        mean_knn_q = knn_q_chunk.mean(1, keepdim=True)

        csls_sim_chunk = 2 * sim_chunk - mean_knn_q - mean_knn_d

        top_indices_chunk = torch.argsort(csls_sim_chunk, dim=1, descending=True)

        for k in ks:
            top_k_preds = top_indices_chunk[:, :k]
            correct_in_top_k = (top_k_preds == gt_chunk.unsqueeze(1)).any(dim=1)
            all_correct_in_top_k[k].append(correct_in_top_k)

    recalls = {}
    for k in ks:
        recalls[f"R@{k}"] = torch.cat(all_correct_in_top_k[k]).float().mean().item()
    return recalls

# -----------------------------------------------------------------
# 7. Training Loop
# -----------------------------------------------------------------
EPOCHS = 60
START_LR = 3e-4
WEIGHT_DECAY = 4e-4

# --- MODIFICATION: Your specific RUN_ID ---
RUN_ID = "VAE_exp3"
FINAL_SAVE_PATH = f"{RUN_ID}_best.pth"
# --- END MODIFICATION ---

val_query_subset = tx_val_t[:5000]
val_indices_subset = img_indices_val[:5000]
val_db_subset = im_train_t_unique

model = VAETranslator(dropout=0.4, hidden_dim=8192, latent_dim=1536, output_dim=1536).to(device)

optimizer = torch.optim.AdamW(model.parameters(), lr=START_LR, weight_decay=WEIGHT_DECAY)
scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=EPOCHS)
scaler = torch.amp.GradScaler('cuda')

print(f"\n--- Starting Giga-VAE (Tighter Brakes, KL_WEIGHT=5e-5) (RUN {RUN_ID}) ---")
print(f"Training (Epochs: {EPOCHS}, LR={START_LR}, WD={WEIGHT_DECAY}, Mixup={MIXUP_ALPHA})...\n")

best_val_r10 = 0.0
for epoch in range(1, EPOCHS + 1):
    model.train()
    total_recon_loss = 0.0
    total_kl_loss = 0.0

    for x_batch, y_batch, img_indices in tqdm(train_loader, desc=f"Epoch {epoch:03d}/{EPOCHS}", leave=False):
        x_batch = x_batch.to(device)
        y_batch = y_batch.to(device)

        idx_shuffle = torch.randperm(x_batch.size(0))
        lam = np.random.beta(MIXUP_ALPHA, MIXUP_ALPHA)
        x_mix = lam * x_batch + (1 - lam) * x_batch[idx_shuffle]
        y_mix = F.normalize(lam * y_batch + (1 - lam) * y_batch[idx_shuffle], p=2, dim=1)

        optimizer.zero_grad()
        with torch.amp.autocast('cuda'):
            y_pred, mu, logvar = model(x_mix)

            # --- 1. Reconstruction Loss ---
            sims_with_tau = y_pred @ y_mix.T / TAU
            labels = torch.arange(y_pred.size(0), device=device)
            loss_con = F.cross_entropy(sims_with_tau, labels)

            with torch.no_grad():
                sims_no_tau = y_pred @ y_mix.T
                positive_mask = torch.eye(y_batch.size(0), dtype=torch.bool, device=device)
                sims_no_tau.masked_fill_(positive_mask, -float('inf'))
                hard_neg_idx = sims_no_tau.argmax(dim=1)
            y_hard_neg = y_mix[hard_neg_idx]
            loss_tri = triplet_loss_fn(y_pred, y_mix, y_hard_neg)

            recon_loss = (LOSS_WEIGHT_CONTRASTIVE * loss_con) + (LOSS_WEIGHT_TRIPLET * loss_tri)

            # --- 2. KL Divergence Loss ---
            kl_loss = calculate_kl_loss(mu, logvar)

            # --- 3. Total Loss ---
            loss = recon_loss + (KL_WEIGHT * kl_loss) # KL_WEIGHT is now 5e-5

        scaler.scale(loss).backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)
        scaler.step(optimizer)
        scaler.update()

        total_recon_loss += recon_loss.item()
        total_kl_loss += kl_loss.item()

    current_lr = scheduler.get_last_lr()[0]
    scheduler.step()
    avg_recon_loss = total_recon_loss / len(train_loader)
    avg_kl_loss = total_kl_loss / len(train_loader)

    # ----- Validation (quick subset) -----
    rec = recall_at_k(model, val_query_subset, val_db_subset, val_indices_subset, chunk_size=1024)
    current_r10 = rec['R@10']

    save_marker = ""
    if current_r10 > best_val_r10:
        best_val_r10 = current_r10
        torch.save(model.state_dict(), FINAL_SAVE_PATH)
        save_marker = "<- Best R@10! Saved."

    print(f"Epoch {epoch:03d}: ReconLoss={avg_recon_loss:.4f} KL_Loss={avg_kl_loss:.2f} (LR={current_lr:.1E}) | R@10(Val)={current_r10:.4f} {save_marker}")

print(f"\n🎯 Training complete. Best model (R@10={best_val_r10:.4f}) saved as {FINAL_SAVE_PATH}")

# -----------------------------------------------------------------
# 8. Inference + Submission
# -----------------------------------------------------------------
print(f"Loading BEST model from {FINAL_SAVE_PATH} for inference...")
model = VAETranslator(dropout=0.4, hidden_dim=8192, latent_dim=1536, output_dim=1536).to(device)
model.load_state_dict(torch.load(FINAL_SAVE_PATH))
model.eval()
print("Best model loaded.")

with torch.no_grad():
    preds_list = []
    for i in tqdm(range(0, len(tx_test_t), 1024), desc="Generating Sub"):
        chunk = tx_test_t[i:i+1024].to(device)
        preds_list.append(model(chunk))

    preds = torch.cat(preds_list, dim=0).cpu().numpy()

test_ids = test_data["captions/ids"].astype(int)
submission = pd.DataFrame({
    "id": test_ids,
    "embedding": [list(map(float, row)) for row in preds]
})

# --- MODIFICATION: Your specific submission filename ---
submission_filename = f"submission_{RUN_ID}.csv"
submission.to_csv(submission_filename, index=False)
print(f"\n✅ {submission_filename} saved successfully.")

# --- Final Validation (on FULL val set, now OOM-safe) ---
print("Calculating final validation scores on full val set...")
rec_full = recall_at_k(model, tx_val_t, im_train_t_unique, img_indices_val, chunk_size=1024)
print("\n--- Full Validation Results ---")
print(f"Validation Recall@1:  {rec_full['R@1']:<8.4f}")
print(f"Validation Recall@5:  {rec_full['R@5']:<8.4f}")
print(f"Validation Recall@10: {rec_full['R@10']:<8.4f}")
print(f"Validation Recall@50: {rec_full['R@50']:<8.4f}")

Using device: cuda
Found 'train.npz' and 'test.clean.npz'. Loading data...
Train shapes: (125000, 1024), (25000, 1536), (125000, 1536)
Test shape: (1500, 1024)
Data preprocessed and normalized (on CPU).
Using CHAMPION ASYMMETRIC loss + VAE KL Loss (weight=5e-05)
Train pairs: 112500, Validation pairs: 12500
Initializing Giga-VAE (hidden_dim=8192, latent_dim=1536)

--- Starting Giga-VAE (Tighter Brakes, KL_WEIGHT=5e-5) (RUN VAE_exp3) ---
Training (Epochs: 60, LR=0.0003, WD=0.0004, Mixup=0.6)...



Epoch 001/60:   0%|          | 0/220 [00:00<?, ?it/s]

CSLS (Pass 1/2):   0%|          | 0/49 [00:00<?, ?it/s]

CSLS (Pass 2/2):   0%|          | 0/5 [00:00<?, ?it/s]

Epoch 001: ReconLoss=2.6204 KL_Loss=1155.09 (LR=3.0E-04) | R@10(Val)=0.3298 <- Best R@10! Saved.


...

Generating Sub:   0%|          | 0/2 [00:00<?, ?it/s]


✅ submission_VAE_exp3.csv saved successfully.
Calculating final validation scores on full val set...


CSLS (Pass 1/2):   0%|          | 0/49 [00:00<?, ?it/s]

CSLS (Pass 2/2):   0%|          | 0/13 [00:00<?, ?it/s]


--- Full Validation Results ---
Validation Recall@1:  0.3066  
Validation Recall@5:  0.5583  
Validation Recall@10: 0.6611  
Validation Recall@50: 0.8569  


## Fine tune to VAE, changing the latent_space from 1546 --> 2048

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader, TensorDataset
import numpy as np
import pandas as pd
from tqdm.auto import tqdm
import os
import time

# --- EXPERIMENT 61: "The Giga-VAE" (Bottleneck) ---
#
# VAE_exp1 (KL=1e-5, latent=1536) is our champion: 0.86241
# We've proven 1e-5 is the best KL_WEIGHT.
# Now we tune the next knob: latent_dim.
#
# 1. Architecture: CHAMPION "Giga-VAE"
# 2. All "Giga-Boss" settings: hidden_dim=8192, DO=0.4, WD=4e-4, Mixup=0.6
# 3. Champion "Brake": KL_WEIGHT = 1e-5
# 4. Loss Change:  *** latent_dim = 1024 *** (Was 1536. Creating a true bottleneck)
# 5. RUN_ID:       *** VAE_exp4 ***
# -----------------------------------------------------------------

# -----------------------------------------------------------------
# 1. Device and data loading
# -----------------------------------------------------------------
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

if not os.path.exists("train.npz") or not os.path.exists("test.clean.npz"):
    print("ERROR: 'train.npz' or 'test.clean.npz' not found.")
    raise FileNotFoundError("Required data files not found.")
else:
    print("Found 'train.npz' and 'test.clean.npz'. Loading data...")

train_data = np.load("train.npz")
test_data  = np.load("test.clean.npz")

tx_train = train_data["captions/embeddings"]
im_train = train_data["images/embeddings"]
tx_test  = test_data["captions/embeddings"]

repeat_factor = len(tx_train) // len(im_train)
im_train_expanded = np.repeat(im_train, repeat_factor, axis=0)
print(f"Train shapes: {tx_train.shape}, {im_train.shape}, {im_train_expanded.shape}")
print(f"Test shape: {tx_test.shape}")

# -----------------------------------------------------------------
# 2. Data preprocessing
# -----------------------------------------------------------------
cpu_device = torch.device("cpu")
tx_train_t = torch.as_tensor(tx_train, dtype=torch.float32, device=cpu_device)
im_train_t_unique = torch.as_tensor(im_train, dtype=torch.float32, device=cpu_device)
tx_test_t  = torch.as_tensor(tx_test,  dtype=torch.float32, device=cpu_device)

tx_mean = tx_train_t.mean(0, keepdim=True)
im_mean = im_train_t_unique.mean(0, keepdim=True)

tx_train_t = F.normalize(tx_train_t - tx_mean, p=2, dim=1)
im_train_t_unique = F.normalize(im_train_t_unique - im_mean, p=2, dim=1)
tx_test_t = F.normalize(tx_test_t - tx_mean, p=2, dim=1)

im_train_exp = torch.as_tensor(im_train_expanded, dtype=torch.float32, device=cpu_device)
im_train_exp = F.normalize(im_train_exp - im_mean, p=2, dim=1)
print("Data preprocessed and normalized (on CPU).")

# -----------------------------------------------------------------
# 3. The Giga-VAE Model (*** MODIFIED latent_dim ***)
# -----------------------------------------------------------------
class VAETranslator(nn.Module):
    # --- MODIFIED: latent_dim is now an argument ---
    def __init__(self, input_dim=1024, hidden_dim=8192, latent_dim=1024, output_dim=1536, dropout=0.4):
        super().__init__()
        self.latent_dim = latent_dim
        print(f"Initializing Giga-VAE (hidden_dim={hidden_dim}, latent_dim={latent_dim})")

        # --- ENCODER (Text -> Distribution) ---
        # 1024 -> 8192 -> 8192 -> (1024 * 2)
        self.encoder = nn.Sequential(
            nn.Linear(input_dim, hidden_dim),
            nn.GELU(),
            nn.LayerNorm(hidden_dim),
            nn.Dropout(dropout),
            nn.Linear(hidden_dim, hidden_dim),
            nn.GELU(),
            nn.LayerNorm(hidden_dim),
            nn.Dropout(dropout),
            nn.Linear(hidden_dim, latent_dim * 2) # Output mu and logvar
        )

        # --- DECODER (Distribution Sample -> Image) ---
        # 1024 -> 8192 -> 8192 -> 1536
        self.decoder = nn.Sequential(
            nn.Linear(latent_dim, hidden_dim),
            nn.GELU(),
            nn.LayerNorm(hidden_dim),
            nn.Dropout(dropout),
            nn.Linear(hidden_dim, hidden_dim),
            nn.GELU(),
            nn.LayerNorm(hidden_dim),
            nn.Dropout(dropout),
            nn.Linear(hidden_dim, output_dim)
        )

    def reparameterize(self, mu, logvar):
        std = torch.exp(0.5 * logvar)
        eps = torch.randn_like(std)
        return mu + eps * std

    def forward(self, x):
        mu_logvar = self.encoder(x)
        mu = mu_logvar[..., :self.latent_dim]
        logvar = mu_logvar[..., self.latent_dim:]

        if self.training:
            z = self.reparameterize(mu, logvar)
            y_pred = self.decoder(z)
            return F.normalize(y_pred, p=2, dim=1), mu, logvar

        y_pred_eval = self.decoder(mu)
        return F.normalize(y_pred_eval, p=2, dim=1)

# -----------------------------------------------------------------
# 4. Loss Functions
# -----------------------------------------------------------------
TAU = 0.01
MARGIN = 0.06
LOSS_WEIGHT_CONTRASTIVE = 0.7
LOSS_WEIGHT_TRIPLET = 0.3
MIXUP_ALPHA = 0.6
KL_WEIGHT = 1e-5 # *** CHAMPION "BRAKE" SETTING ***

triplet_loss_fn = nn.TripletMarginWithDistanceLoss(
    distance_function=lambda x, y: 1 - F.cosine_similarity(x, y),
    margin=MARGIN
)
print(f"Using CHAMPION ASYMMETRIC loss + VAE KL Loss (weight={KL_WEIGHT})")

def calculate_kl_loss(mu, logvar):
    kl_loss = -0.5 * torch.sum(1 + logvar - mu.pow(2) - logvar.exp())
    return kl_loss / mu.size(0)

# -----------------------------------------------------------------
# 5. Validation split
# -----------------------------------------------------------------
N = len(tx_train_t)
val_size = int(0.1 * N)
idx_cpu = torch.randperm(N, device="cpu")
val_idx, train_idx = idx_cpu[:val_size], idx_cpu[val_size:]

img_indices_train = (train_idx // 5)
img_indices_val = (val_idx // 5)

tx_val_t, im_val_t = tx_train_t[val_idx], im_train_exp[val_idx]
tx_train_t_sub, im_train_exp_sub = tx_train_t[train_idx], im_train_exp[train_idx]

train_dataset = TensorDataset(tx_train_t_sub, im_train_exp_sub, img_indices_train)
train_loader = DataLoader(train_dataset, batch_size=512, shuffle=True, num_workers=0)
print(f"Train pairs: {len(train_dataset)}, Validation pairs: {len(val_idx)}")

# -----------------------------------------------------------------
# 6. Memory-Safe Recall@K Utility
# -----------------------------------------------------------------
@torch.no_grad()
def recall_at_k(model, tx_queries, im_database, query_img_indices, chunk_size=1024, ks=(1, 5, 10, 50), k_csls=10):
    model.eval()
    device = next(model.parameters()).device
    all_correct_in_top_k = {k: [] for k in ks}

    Q_embed_list = []
    for i in range(0, len(tx_queries), chunk_size):
        chunk = tx_queries[i:i+chunk_size].to(device)
        Q_embed_list.append(model(chunk))
    Q_embed = torch.cat(Q_embed_list, dim=0)

    D_embed = im_database.to(device)

    mean_knn_d_list = []
    for i in tqdm(range(0, len(D_embed), 512), desc="CSLS (Pass 1/2)", leave=False):
        sim_T_chunk = D_embed[i:i+512] @ Q_embed.T
        knn_d_chunk = torch.topk(sim_T_chunk, k=k_csls, dim=1).values
        mean_knn_d_list.append(knn_d_chunk.mean(1))

    mean_knn_d = torch.cat(mean_knn_d_list, dim=0).unsqueeze(0)

    gt = query_img_indices.to(device)

    for i in tqdm(range(0, len(Q_embed), chunk_size), desc="CSLS (Pass 2/2)", leave=False):
        sim_chunk = Q_embed[i:i+chunk_size] @ D_embed.T
        gt_chunk = gt[i:i+chunk_size]

        knn_q_chunk = torch.topk(sim_chunk, k=k_csls, dim=1).values
        mean_knn_q = knn_q_chunk.mean(1, keepdim=True)

        csls_sim_chunk = 2 * sim_chunk - mean_knn_q - mean_knn_d

        top_indices_chunk = torch.argsort(csls_sim_chunk, dim=1, descending=True)

        for k in ks:
            top_k_preds = top_indices_chunk[:, :k]
            correct_in_top_k = (top_k_preds == gt_chunk.unsqueeze(1)).any(dim=1)
            all_correct_in_top_k[k].append(correct_in_top_k)

    recalls = {}
    for k in ks:
        recalls[f"R@{k}"] = torch.cat(all_correct_in_top_k[k]).float().mean().item()
    return recalls

# -----------------------------------------------------------------
# 7. Training Loop
# -----------------------------------------------------------------
EPOCHS = 60
START_LR = 3e-4
WEIGHT_DECAY = 4e-4

# --- MODIFICATION: Your specific RUN_ID ---
RUN_ID = "VAE_exp4"
FINAL_SAVE_PATH = f"{RUN_ID}_best.pth"
# --- END MODIFICATION ---

val_query_subset = tx_val_t[:5000]
val_indices_subset = img_indices_val[:5000]
val_db_subset = im_train_t_unique

# --- MODIFICATION: Initialize model with latent_dim=1024 ---
model = VAETranslator(dropout=0.4, hidden_dim=8192, latent_dim=1024, output_dim=1536).to(device)

optimizer = torch.optim.AdamW(model.parameters(), lr=START_LR, weight_decay=WEIGHT_DECAY)
scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=EPOCHS)
scaler = torch.amp.GradScaler('cuda')

print(f"\n--- Starting Giga-VAE (Bottleneck, latent_dim=1024) (RUN {RUN_ID}) ---")
print(f"Training (Epochs: {EPOCHS}, LR={START_LR}, WD={WEIGHT_DECAY}, Mixup={MIXUP_ALPHA})...\n")

best_val_r10 = 0.0
for epoch in range(1, EPOCHS + 1):
    model.train()
    total_recon_loss = 0.0
    total_kl_loss = 0.0

    for x_batch, y_batch, img_indices in tqdm(train_loader, desc=f"Epoch {epoch:03d}/{EPOCHS}", leave=False):
        x_batch = x_batch.to(device)
        y_batch = y_batch.to(device)

        idx_shuffle = torch.randperm(x_batch.size(0))
        lam = np.random.beta(MIXUP_ALPHA, MIXUP_ALPHA)
        x_mix = lam * x_batch + (1 - lam) * x_batch[idx_shuffle]
        y_mix = F.normalize(lam * y_batch + (1 - lam) * y_batch[idx_shuffle], p=2, dim=1)

        optimizer.zero_grad()
        with torch.amp.autocast('cuda'):
            y_pred, mu, logvar = model(x_mix)

            # --- 1. Reconstruction Loss ---
            sims_with_tau = y_pred @ y_mix.T / TAU
            labels = torch.arange(y_pred.size(0), device=device)
            loss_con = F.cross_entropy(sims_with_tau, labels)

            with torch.no_grad():
                sims_no_tau = y_pred @ y_mix.T
                positive_mask = torch.eye(y_batch.size(0), dtype=torch.bool, device=device)
                sims_no_tau.masked_fill_(positive_mask, -float('inf'))
                hard_neg_idx = sims_no_tau.argmax(dim=1)
            y_hard_neg = y_mix[hard_neg_idx]
            loss_tri = triplet_loss_fn(y_pred, y_mix, y_hard_neg)

            recon_loss = (LOSS_WEIGHT_CONTRASTIVE * loss_con) + (LOSS_WEIGHT_TRIPLET * loss_tri)

            # --- 2. KL Divergence Loss ---
            kl_loss = calculate_kl_loss(mu, logvar)

            # --- 3. Total Loss ---
            loss = recon_loss + (KL_WEIGHT * kl_loss) # KL_WEIGHT is 1e-5

        scaler.scale(loss).backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)
        scaler.step(optimizer)
        scaler.update()

        total_recon_loss += recon_loss.item()
        total_kl_loss += kl_loss.item()

    current_lr = scheduler.get_last_lr()[0]
    scheduler.step()
    avg_recon_loss = total_recon_loss / len(train_loader)
    avg_kl_loss = total_kl_loss / len(train_loader)

    # ----- Validation (quick subset) -----
    rec = recall_at_k(model, val_query_subset, val_db_subset, val_indices_subset, chunk_size=1024)
    current_r10 = rec['R@10']

    save_marker = ""
    if current_r10 > best_val_r10:
        best_val_r10 = current_r10
        torch.save(model.state_dict(), FINAL_SAVE_PATH)
        save_marker = "<- Best R@10! Saved."

    print(f"Epoch {epoch:03d}: ReconLoss={avg_recon_loss:.4f} KL_Loss={avg_kl_loss:.2f} (LR={current_lr:.1E}) | R@10(Val)={current_r10:.4f} {save_marker}")

print(f"\n🎯 Training complete. Best model (R@10={best_val_r10:.4f}) saved as {FINAL_SAVE_PATH}")

# -----------------------------------------------------------------
# 8. Inference + Submission
# -----------------------------------------------------------------
print(f"Loading BEST model from {FINAL_SAVE_PATH} for inference...")
# --- MODIFICATION: Load model with latent_dim=1024 ---
model = VAETranslator(dropout=0.4, hidden_dim=8192, latent_dim=1024, output_dim=1536).to(device)
model.load_state_dict(torch.load(FINAL_SAVE_PATH))
model.eval()
print("Best model loaded.")

with torch.no_grad():
    preds_list = []
    for i in tqdm(range(0, len(tx_test_t), 1024), desc="Generating Sub"):
        chunk = tx_test_t[i:i+1024].to(device)
        preds_list.append(model(chunk))

    preds = torch.cat(preds_list, dim=0).cpu().numpy()

test_ids = test_data["captions/ids"].astype(int)
submission = pd.DataFrame({
    "id": test_ids,
    "embedding": [list(map(float, row)) for row in preds]
})

submission_filename = f"submission_{RUN_ID}.csv"
submission.to_csv(submission_filename, index=False)
print(f"\n✅ {submission_filename} saved successfully.")

# --- Final Validation (on FULL val set, now OOM-safe) ---
print("Calculating final validation scores on full val set...")
rec_full = recall_at_k(model, tx_val_t, im_train_t_unique, img_indices_val, chunk_size=1024)
print("\n--- Full Validation Results ---")
print(f"Validation Recall@1:  {rec_full['R@1']:<8.4f}")
print(f"Validation Recall@5:  {rec_full['R@5']:<8.4f}")
print(f"Validation Recall@10: {rec_full['R@10']:<8.4f}")
print(f"Validation Recall@50: {rec_full['R@50']:<8.4f}")